# Agentes AutoGen em Produção: Observabilidade e Avaliação

Neste tutorial, vamos aprender a **monitorizar os passos internos (traços) dos [agentes Autogen](https://github.com/microsoft/autogen)** e a **avaliar o seu desempenho** utilizando o [Langfuse](https://langfuse.com).

Este guia aborda métricas de avaliação **online** e **offline** usadas por equipas para colocar agentes em produção de forma rápida e confiável.

**Por que a Avaliação de Agentes de IA é importante:**
- Depurar problemas quando as tarefas falham ou produzem resultados abaixo do esperado
- Monitorizar custos e desempenho em tempo real
- Melhorar a fiabilidade e segurança através de feedback contínuo


## Passo 1: Definir Variáveis de Ambiente

Obtenha as suas chaves API do Langfuse ao inscrever-se no [Langfuse Cloud](https://cloud.langfuse.com/) ou ao [hospedar Langfuse por conta própria](https://langfuse.com/self-hosting).

_**Nota:** Utilizadores que hospedam por conta própria podem usar [módulos Terraform](https://langfuse.com/self-hosting/azure) para implementar o Langfuse no Azure. Alternativamente, pode implementar o Langfuse no Kubernetes utilizando o [Helm chart](https://langfuse.com/self-hosting/kubernetes-helm)._


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

Com as variáveis de ambiente definidas, podemos agora inicializar o cliente Langfuse. `get_client()` inicializa o cliente Langfuse utilizando as credenciais fornecidas nas variáveis de ambiente.


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## Passo 2: Inicializar a Instrumentação OpenLit

Agora, vamos inicializar a instrumentação [OpenLit](https://github.com/openlit/openlit). O OpenLit captura automaticamente as operações do AutoGen e exporta os spans do OpenTelemetry (OTel) para o Langfuse.


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## Passo 3: Execute o seu agente

Agora configuramos um agente de múltiplas interações para testar a nossa instrumentação.


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### Estrutura do Rasto

O Langfuse regista um **rasto** que contém **spans**, que representam cada etapa da lógica do seu agente. Aqui, o rasto inclui a execução geral do agente e sub-spans para:
- O agente de planeamento de refeições
- Os agentes nutricionistas

Pode inspecioná-los para ver exatamente onde o tempo é gasto, quantos tokens são utilizados, entre outros detalhes:

![Árvore de rastos no Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[Link para o rasto](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## Avaliação Online

A Avaliação Online refere-se à avaliação do agente num ambiente real e em tempo real, ou seja, durante o uso efetivo em produção. Isto envolve monitorizar o desempenho do agente em interações reais com utilizadores e analisar continuamente os resultados.

### Métricas Comuns para Monitorizar em Produção

1. **Custos** — A instrumentação captura o uso de tokens, que pode ser transformado em custos aproximados ao atribuir um preço por token.
2. **Latência** — Observe o tempo necessário para completar cada etapa ou toda a execução.
3. **Feedback do Utilizador** — Os utilizadores podem fornecer feedback direto (gosto/não gosto) para ajudar a refinar ou corrigir o agente.
4. **LLM-como-Juiz** — Utilize um LLM separado para avaliar a saída do seu agente em tempo quase real (por exemplo, verificando toxicidade ou correção).

Abaixo, mostramos exemplos destas métricas.


#### 1. Custos

Abaixo está uma captura de ecrã que mostra a utilização de chamadas para `gpt-4o-mini`. Isto é útil para identificar etapas dispendiosas e otimizar o seu agente.

![Custos](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[Link para o rastreio](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. Latência

Também podemos verificar quanto tempo levou para completar cada etapa. No exemplo abaixo, a execução completa levou cerca de 3 segundos, que podem ser divididos por etapa. Isso ajuda a identificar pontos de estrangulamento e a otimizar o seu agente.

![Latência](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[Link para o rastreio](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. Feedback do Utilizador

Se o seu agente estiver integrado numa interface de utilizador, pode registar feedback direto dos utilizadores (como um "gosto" ou "não gosto" numa interface de chat).


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

O feedback do utilizador é então capturado no Langfuse:

![O feedback do utilizador está a ser capturado no Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. Avaliação Automática com LLM como Juiz

LLM como Juiz é outra forma de avaliar automaticamente o resultado gerado pelo seu agente. Pode configurar uma chamada separada ao LLM para avaliar a correção, toxicidade, estilo ou qualquer outro critério que considere importante.

**Fluxo de Trabalho**:
1. Define um **Template de Avaliação**, por exemplo, "Verificar se o texto é tóxico."
2. Define um modelo que será usado como modelo juiz; neste caso, `gpt-4o-mini` consultado via Azure.
3. Cada vez que o seu agente gera um resultado, passa esse resultado ao LLM "juiz" com o template.
4. O LLM juiz responde com uma classificação ou etiqueta que regista na sua ferramenta de observabilidade.

Exemplo do Langfuse:

![LLM como Avaliador](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

Pode-se observar que a resposta deste exemplo é avaliada como "não tóxica".

![Pontuação de Avaliação do LLM como Juiz](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. Visão Geral das Métricas de Observabilidade

Todas estas métricas podem ser visualizadas em conjunto em dashboards. Isto permite-lhe ver rapidamente como o seu agente se comporta em várias sessões e ajuda a acompanhar métricas de qualidade ao longo do tempo.

![Visão geral das métricas de observabilidade](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## Avaliação Offline

A avaliação online é essencial para obter feedback em tempo real, mas também é necessário realizar **avaliação offline**—verificações sistemáticas antes ou durante o desenvolvimento. Isto ajuda a garantir qualidade e fiabilidade antes de implementar alterações em produção.


### Avaliação do Conjunto de Dados

Na avaliação offline, normalmente:
1. Tem um conjunto de dados de referência (com pares de perguntas e respostas esperadas)
2. Executa o seu agente nesse conjunto de dados
3. Compara os resultados obtidos com os resultados esperados ou utiliza um mecanismo adicional de pontuação

Abaixo, demonstramos esta abordagem com o [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset), que contém perguntas e respostas esperadas.


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

Em seguida, criamos uma entidade de conjunto de dados no Langfuse para acompanhar as execuções. Depois, adicionamos cada item do conjunto de dados ao sistema.


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![Itens do conjunto de dados no Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### Executar o Agente no Conjunto de Dados

Primeiro, montamos um agente Autogen simples que responde a perguntas utilizando modelos do Azure OpenAI.


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

Em seguida, definimos uma função auxiliar `my_agent()`.


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

Finalmente, percorremos cada item do conjunto de dados, executamos o agente e ligamos o traço ao item do conjunto de dados. Podemos também anexar uma pontuação de avaliação rápida, se desejado.


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

REGRAS IMPORTANTES:  
1. NÃO adicione '''markdown ou quaisquer outras etiquetas à volta da tradução  
2. Certifique-se de que a tradução não soa demasiado literal  
3. Traduza também os comentários  
4. Este ficheiro está escrito em formato Markdown - não o trate como XML ou HTML  
5. Não traduza:  
   - [!NOTE], [!WARNING], [!TIP], [!IMPORTANT], [!CAUTION]  
   - Nomes de variáveis, nomes de funções, nomes de classes  
   - Marcadores de posição como @@INLINE_CODE_x@@ ou @@CODE_BLOCK_x@@  
   - URLs ou caminhos  
6. Mantenha toda a formatação Markdown original intacta  
7. Devolva APENAS o conteúdo traduzido sem quaisquer etiquetas ou marcações adicionais  

Pode repetir este processo com diferentes configurações de agentes, tais como:  
- Modelos (gpt-4o-mini, gpt-4.1, etc.)  
- Prompts  
- Ferramentas (com pesquisa vs. sem pesquisa)  
- Complexidade do agente (multiagente vs. agente único)  

Depois, compare-os lado a lado no Langfuse. Neste exemplo, executei o agente 3 vezes nas 25 perguntas do conjunto de dados. Para cada execução, utilizei um modelo diferente do Azure OpenAI. Pode verificar que a quantidade de perguntas respondidas corretamente melhora ao usar um modelo maior (como era de esperar). A pontuação `correct_answer` é criada por um [Avaliador LLM-as-a-Judge](https://langfuse.com/docs/scores/model-based-evals) configurado para avaliar a correção da pergunta com base na resposta de exemplo fornecida no conjunto de dados.  

![Visão geral da execução do conjunto de dados](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)  
![Comparação de execução do conjunto de dados](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)  



---

**Aviso Legal**:  
Este documento foi traduzido utilizando o serviço de tradução por IA [Co-op Translator](https://github.com/Azure/co-op-translator). Embora nos esforcemos para garantir a precisão, é importante notar que traduções automáticas podem conter erros ou imprecisões. O documento original na sua língua nativa deve ser considerado a fonte autoritária. Para informações críticas, recomenda-se a tradução profissional realizada por humanos. Não nos responsabilizamos por quaisquer mal-entendidos ou interpretações incorretas decorrentes do uso desta tradução.
